In [ ]:
from google.colab import drive
drive.mount('/content/drive')

In [ ]:
!apt -y install -qq aria2
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/camenduru/joy-caption-alpha-one/raw/main/text_model/adapter_config.json -d /content/joy/text_model -o adapter_config.json
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/camenduru/joy-caption-alpha-one/resolve/main/text_model/adapter_model.safetensors -d /content/joy/text_model -o adapter_model.safetensors
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/camenduru/joy-caption-alpha-one/resolve/main/clip_model.pt -d /content/joy -o clip_model.pt
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/camenduru/joy-caption-alpha-one/raw/main/config.yaml -d /content/joy -o config.yaml
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/camenduru/joy-caption-alpha-one/resolve/main/image_adapter.pt -d /content/joy -o image_adapter.pt

!apt -y install -qq aria2
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/camenduru/joy-caption-alpha-one/raw/main/text_model/adapter_config.json -d /content/joy/text_model -o adapter_config.json
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/camenduru/joy-caption-alpha-one/resolve/main/text_model/adapter_model.safetensors -d /content/joy/text_model -o adapter_model.safetensors
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/camenduru/joy-caption-alpha-one/resolve/main/clip_model.pt -d /content/joy -o clip_model.pt
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/camenduru/joy-caption-alpha-one/raw/main/config.yaml -d /content/joy -o config.yaml
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/camenduru/joy-caption-alpha-one/resolve/main/image_adapter.pt -d /content/joy -o image_adapter.pt

# @markdown Use a custom prompt to instruct the image captioning model
custom_prompt = 'Write a natural language prompt using e621 and/or danbooru tags in multiple sentences of 400 words or tags' # @param {type:'string'}
enable_custom_prompt = False # @param {type:'boolean'}
if not enable_custom_prompt: custom_prompt = 'Describe the image in 400 words'
!pip install peft bitsandbytes
!pip install hf_xet
from huggingface_hub import InferenceClient
from torch import nn
from transformers import AutoModel, BitsAndBytesConfig, AutoProcessor, AutoTokenizer, PreTrainedTokenizer, PreTrainedTokenizerFast, AutoModelForCausalLM
import torch
import torch.amp.autocast_mode
from PIL import Image
import os
import torchvision.transforms.functional as TVF

CLIP_PATH = "google/siglip-so400m-patch14-384"
MODEL_PATH = "unsloth/Meta-Llama-3.1-8B-bnb-4bit"
CAPTION_TYPE_MAP = {
    ("descriptive", "formal", False, False): [f"{custom_prompt}"],
    ("descriptive", "formal", False, True): ["Write a descriptive caption for this image in a formal tone within {word_count} words."],
    ("descriptive", "formal", True, False): ["Write a {length} descriptive caption for this image in a formal tone."],
    ("descriptive", "informal", False, False): ["Write a descriptive caption for this image in a casual tone."],
    ("descriptive", "informal", False, True): ["Write a descriptive caption for this image in a casual tone within {word_count} words."],
    ("descriptive", "informal", True, False): ["Write a {length} descriptive caption for this image in a casual tone."],
    ("training_prompt", "formal", False, False): ["Write a stable diffusion prompt for this image."],
    ("training_prompt", "formal", False, True): ["Write a stable diffusion prompt for this image within {word_count} words."],
    ("training_prompt", "formal", True, False): ["Write a {length} stable diffusion prompt for this image."],
    ("rng-tags", "formal", False, False): ["Write a list of Booru tags for this image."],
    ("rng-tags", "formal", False, True): ["Write a list of Booru tags for this image within {word_count} words."],
    ("rng-tags", "formal", True, False): ["Write a {length} list of Booru tags for this image."],
}

class ImageAdapter(nn.Module):
	def __init__(self, input_features: int, output_features: int, ln1: bool, pos_emb: bool, num_image_tokens: int, deep_extract: bool):
		super().__init__()
		self.deep_extract = deep_extract
		if self.deep_extract:
			input_features = input_features * 5
		self.linear1 = nn.Linear(input_features, output_features)
		self.activation = nn.GELU()
		self.linear2 = nn.Linear(output_features, output_features)
		self.ln1 = nn.Identity() if not ln1 else nn.LayerNorm(input_features)
		self.pos_emb = None if not pos_emb else nn.Parameter(torch.zeros(num_image_tokens, input_features))
		self.other_tokens = nn.Embedding(3, output_features)
		self.other_tokens.weight.data.normal_(mean=0.0, std=0.02)   # Matches HF's implementation of llama3
	def forward(self, vision_outputs: torch.Tensor):
		if self.deep_extract:
			x = torch.concat((
				vision_outputs[-2],
				vision_outputs[3],
				vision_outputs[7],
				vision_outputs[13],
				vision_outputs[20],
			), dim=-1)
			assert len(x.shape) == 3, f"Expected 3, got {len(x.shape)}"  # batch, tokens, features
			assert x.shape[-1] == vision_outputs[-2].shape[-1] * 5, f"Expected {vision_outputs[-2].shape[-1] * 5}, got {x.shape[-1]}"
		else:
			x = vision_outputs[-2]
		x = self.ln1(x)
		if self.pos_emb is not None:
			assert x.shape[-2:] == self.pos_emb.shape, f"Expected {self.pos_emb.shape}, got {x.shape[-2:]}"
			x = x + self.pos_emb
		x = self.linear1(x)
		x = self.activation(x)
		x = self.linear2(x)
		other_tokens = self.other_tokens(torch.tensor([0, 1], device=self.other_tokens.weight.device).expand(x.shape[0], -1))
		assert other_tokens.shape == (x.shape[0], 2, x.shape[2]), f"Expected {(x.shape[0], 2, x.shape[2])}, got {other_tokens.shape}"
		x = torch.cat((other_tokens[:, 0:1], x, other_tokens[:, 1:2]), dim=1)
		return x
	def get_eot_embedding(self):
		return self.other_tokens(torch.tensor([2], device=self.other_tokens.weight.device)).squeeze(0)

clip_processor = AutoProcessor.from_pretrained(CLIP_PATH)
clip_model = AutoModel.from_pretrained(CLIP_PATH)
clip_model = clip_model.vision_model
checkpoint = torch.load("/content/joy/clip_model.pt", map_location='cpu')
checkpoint = {k.replace("_orig_mod.module.", ""): v for k, v in checkpoint.items()}
clip_model.load_state_dict(checkpoint)
# del checkpoint
clip_model.eval()
clip_model.requires_grad_(False)
clip_model.to("cuda")
tokenizer = AutoTokenizer.from_pretrained(f'{MODEL_PATH}')
#tokenizer = AutoTokenizer.from_pretrained("unsloth/Meta-Llama-3.1-8B-bnb-4bit")
assert isinstance(tokenizer, PreTrainedTokenizer) or isinstance(tokenizer, PreTrainedTokenizerFast), f"Tokenizer is of type {type(tokenizer)}"
text_model = AutoModelForCausalLM.from_pretrained(MODEL_PATH, quantization_config = BitsAndBytesConfig(load_in_8bit=True), device_map="auto", torch_dtype=torch.bfloat16)
text_model.load_adapter("/content/joy/text_model")
text_model.eval()
image_adapter = ImageAdapter(clip_model.config.hidden_size, text_model.config.hidden_size, False, False, 38, False)
image_adapter.load_state_dict(torch.load("/content/joy/image_adapter.pt", map_location="cpu"))
image_adapter.eval()
image_adapter.to("cuda")

In [ ]:
#urls=["https://imx.to/i/67yoyb","https://imx.to/i/67yovt","https://imx.to/i/67yozl","https://imx.to/i/67yows","https://imx.to/i/67youk","https://imx.to/i/67yoxy","https://imx.to/i/67yoz9","https://imx.to/i/67yown","https://imx.to/i/67youc","https://imx.to/i/67yovj","https://imx.to/i/67yoyw","https://imx.to/i/67yowf","https://imx.to/i/67yp0d","https://imx.to/i/67yoxb","https://imx.to/i/67yov6","https://imx.to/i/67yoym","https://imx.to/i/67yozz","https://imx.to/i/67yox4","https://imx.to/i/67yow1","https://imx.to/i/67yowz","https://imx.to/i/67youn","https://imx.to/i/67yovy","https://imx.to/i/67yozm","https://imx.to/i/67yowt","https://imx.to/i/67yoxz","https://imx.to/i/67yovn","https://imx.to/i/67yozb","https://imx.to/i/67you7","https://imx.to/i/67yoxc","https://imx.to/i/67yov4","https://imx.to/i/67yow6","https://imx.to/i/67yozv","https://imx.to/i/67yovv","https://imx.to/i/67yozo","https://imx.to/i/67youh","https://imx.to/i/67yowm","https://imx.to/i/67youd","https://imx.to/i/67yoxr","https://imx.to/i/67yovf","https://imx.to/i/67yoyx","https://imx.to/i/67yowg","https://imx.to/i/67yp0e","https://imx.to/i/67yoxh","https://imx.to/i/67yov7","https://imx.to/i/67yoyl","https://imx.to/i/67yp02","https://imx.to/i/67yox3","https://imx.to/i/67youw","https://imx.to/i/67yoyh","https://imx.to/i/67yow2","https://imx.to/i/67yozu","https://imx.to/i/67yox0","https://imx.to/i/67xj9p","https://imx.to/i/67yowo","https://imx.to/i/67yoxk","https://imx.to/i/67yovi","https://imx.to/i/67xjad","https://imx.to/i/67yoyo","https://imx.to/i/67yow7","https://imx.to/i/67youx","https://imx.to/i/67xjar","https://imx.to/i/67xja5","https://imx.to/i/67you6","https://imx.to/i/67yoxt","https://imx.to/i/67yoyy","https://imx.to/i/67yp0f","https://imx.to/i/67yoxl","https://imx.to/i/67yow8","https://imx.to/i/67xja3","https://imx.to/i/67yp04","https://imx.to/i/67youv","https://imx.to/i/67yozw","https://imx.to/i/67xjaj","https://imx.to/i/67yoye","https://imx.to/i/67yowy","https://imx.to/i/67youl","https://imx.to/i/67xjac","https://imx.to/i/67yoy4","https://imx.to/i/67yovq","https://imx.to/i/67yozf","https://imx.to/i/67yowq","https://imx.to/i/67youb","https://imx.to/i/67yove","https://imx.to/i/67yoz3","https://imx.to/i/67xja1","https://imx.to/i/67yowi","https://imx.to/i/67yoxm","https://imx.to/i/67yov9","https://imx.to/i/67yoyq","https://imx.to/i/67yp05","https://imx.to/i/67youz","https://imx.to/i/67yozx","https://imx.to/i/67yoyf","https://imx.to/i/67xjaa","https://imx.to/i/67yovx","https://imx.to/i/67yozq","https://imx.to/i/67yovr","https://imx.to/i/67xja6","https://imx.to/i/67yoxn","https://imx.to/i/67yovc","https://imx.to/i/67yow9","https://imx.to/i/67yox8","https://imx.to/i/67yoyj","https://imx.to/i/67yow5","https://imx.to/i/67xjao","https://imx.to/i/67yox1","https://imx.to/i/67youq","https://imx.to/i/67yoyg","https://imx.to/i/67youi","https://imx.to/i/67yovs","https://imx.to/i/67yoxv","https://imx.to/i/67yoz5","https://imx.to/i/67yp0g","https://imx.to/i/67yoxo","https://imx.to/i/67yoys","https://imx.to/i/67yowa","https://imx.to/i/67yp09","https://imx.to/i/67yox7","https://imx.to/i/67youy","https://imx.to/i/67yoyk","https://imx.to/i/67yp00","https://imx.to/i/67yozr","https://imx.to/i/67yowx","https://imx.to/i/67youo","https://imx.to/i/67yoy5","https://imx.to/i/67xja9","https://imx.to/i/67yoxp","https://imx.to/i/67yoyt","https://imx.to/i/67yp08","https://imx.to/i/67yoyn","https://imx.to/i/67xja7","https://imx.to/i/67yozs","https://imx.to/i/67yoy9","https://imx.to/i/67yoze","https://imx.to/i/67youg","https://imx.to/i/67yous","https://imx.to/i/67xjal","https://imx.to/i/67yoy8","https://imx.to/i/67yovu","https://imx.to/i/67yoxx","https://imx.to/i/67yoz7","https://imx.to/i/67xj9s","https://imx.to/i/67yoyv","https://imx.to/i/67yovp","https://imx.to/i/67yoww","https://imx.to/i/67yoy1","https://imx.to/i/67you8","https://imx.to/i/67yoyr","https://imx.to/i/67yp0b","https://imx.to/i/67xjaq","https://imx.to/i/67yovh","https://imx.to/i/67yoyu","https://imx.to/i/67yowc","https://imx.to/i/67yp0c","https://imx.to/i/67yov3","https://imx.to/i/67yox2","https://imx.to/i/67yout","https://imx.to/i/67xjaf","https://imx.to/i/67yoya","https://imx.to/i/67yowk","https://imx.to/i/67you9","https://imx.to/i/67yoxq","https://imx.to/i/67yov2","https://imx.to/i/67youp","https://imx.to/i/67yovz","https://imx.to/i/67yowr","https://imx.to/i/67youf","https://imx.to/i/67yoxw","https://imx.to/i/67yovk","https://imx.to/i/67xjab","https://imx.to/i/67yow0","https://imx.to/i/67yozt","https://imx.to/i/67yoyc","https://imx.to/i/67yozk","https://imx.to/i/67yowl","https://imx.to/i/67yov1","https://imx.to/i/67yoy2","https://imx.to/i/67yovm","https://imx.to/i/67yozd","https://imx.to/i/67yowp","https://imx.to/i/67youe","https://imx.to/i/67xj9t","https://imx.to/i/67xja2","https://imx.to/i/67xjai","https://imx.to/i/67xjah","https://imx.to/i/67xjas","https://imx.to/i/67xja8","https://imx.to/i/67xjae","https://imx.to/i/67xja4","https://imx.to/i/67xjap","https://imx.to/i/67xj9n","https://imx.to/i/67xjat","https://imx.to/i/67xj9z","https://imx.to/i/67xj9r","https://imx.to/i/67xj9w","https://imx.to/i/67xj9x","https://imx.to/i/67xja0","https://imx.to/i/67xj9o","https://imx.to/i/67xj9q","https://imx.to/i/67xj9u","https://imx.to/i/67xjak","https://imx.to/i/67xj9v","https://imx.to/i/67xjam","https://imx.to/i/67xj9y","https://imx.to/i/67xjan","https://imx.to/i/67xjag","https://imx.to/i/67yovd","https://imx.to/i/67yowd","https://imx.to/i/67yp0a","https://imx.to/i/67yox9","https://imx.to/i/67yoy6","https://imx.to/i/67yp01","https://imx.to/i/67yovg","https://imx.to/i/67yowe","https://imx.to/i/67your","https://imx.to/i/67yoyd","https://imx.to/i/67yoy0","https://imx.to/i/67yoza","https://imx.to/i/67you5","https://imx.to/i/67yoxs","https://imx.to/i/67yp0h","https://imx.to/i/67yoxi","https://imx.to/i/67yov5","https://imx.to/i/67yoyp","https://imx.to/i/67yp03","https://imx.to/i/67yox5","https://imx.to/i/67yov0","https://imx.to/i/67yoyi","https://imx.to/i/67yozn","https://imx.to/i/67yowv","https://imx.to/i/67yovo","https://imx.to/i/67yozc","https://imx.to/i/67youa","https://imx.to/i/67yoxu","https://imx.to/i/67yoz4","https://imx.to/i/67yowh","https://imx.to/i/67yoxj","https://imx.to/i/67yov8","https://imx.to/i/67yp06","https://imx.to/i/67youu","https://imx.to/i/67yow3","https://imx.to/i/67yozy","https://imx.to/i/67yozp","https://imx.to/i/67yoy3","https://imx.to/i/67yovw","https://imx.to/i/67yoz6","https://imx.to/i/67yova","https://imx.to/i/67yox6","https://imx.to/i/67yowj","https://imx.to/i/67yp0i","https://imx.to/i/67yowb","https://imx.to/i/67yovl","https://imx.to/i/67yoz8","https://imx.to/i/67yoxa","https://imx.to/i/67youm"]
#!pip install wget
%cd /content/
for url in urls:
    # Extract the image ID from the URL
    image_id = url.split('/')[-1]
    # Construct the wget command
    !wget {url} -O '{image_id}.jpg'
    #print(command)






In [ ]:



# @markdown Use a custom prompt to instruct the image captioning model
custom_prompt = '' # @param {type:'string'}
enable_custom_prompt = True # @param {type:'boolean'}
if not enable_custom_prompt: custom_prompt = 'Describe the image in 400 words'

CAPTION_TYPE_MAP = {
    ("descriptive", "formal", False, False): [f"{custom_prompt}"],
    ("descriptive", "formal", False, True): ["Write a descriptive caption for this image in a formal tone within {word_count} words."],
    ("descriptive", "formal", True, False): ["Write a {length} descriptive caption for this image in a formal tone."],
    ("descriptive", "informal", False, False): ["Write a descriptive caption for this image in a casual tone."],
    ("descriptive", "informal", False, True): ["Write a descriptive caption for this image in a casual tone within {word_count} words."],
    ("descriptive", "informal", True, False): ["Write a {length} descriptive caption for this image in a casual tone."],
    ("training_prompt", "formal", False, False): ["Write a stable diffusion prompt for this image."],
    ("training_prompt", "formal", False, True): ["Write a stable diffusion prompt for this image within {word_count} words."],
    ("training_prompt", "formal", True, False): ["Write a {length} stable diffusion prompt for this image."],
    ("rng-tags", "formal", False, False): ["Write a list of Booru tags for this image."],
    ("rng-tags", "formal", False, True): ["Write a list of Booru tags for this image within {word_count} words."],
    ("rng-tags", "formal", True, False): ["Write a {length} list of Booru tags for this image."],
}

In [6]:
# @markdown higher temperature = prompt creativity (default 0.6) <br> higher top_p = higher noise reduction in latent embedding (default 0.9)
temperature = 1.75 # @param {type:'slider',min:0.5,max:4.0,step:0.05}
top_p = 0.75 # @param {type:'slider',min:0.1,max:0.95,step:0.05}
temperature = float(temperature)
top_p = float(top_p)
prompt_str = 'invent words you think about when seeing this image'
#-----#
num=1

@torch.no_grad()
def stream_chat(input_image: Image.Image, caption_type: str, caption_tone: str, caption_length: str | int) -> str:
    torch.cuda.empty_cache()
    length = None if caption_length == "any" else caption_length
    if isinstance(length, str):
        try:
            length = int(length)
        except ValueError:
            pass
    if caption_type == "rng-tags" or caption_type == "training_prompt":
        caption_tone = "formal"
    prompt_key = (caption_type, caption_tone, isinstance(length, str), isinstance(length, int))
    if prompt_key not in CAPTION_TYPE_MAP:
        raise ValueError(f"Invalid caption type: {prompt_key}")
    prompt_str = CAPTION_TYPE_MAP[prompt_key][0].format(length=length, word_count=length)
    print(f"Prompt: {prompt_str}")
    image = input_image.resize((384, 384), Image.LANCZOS)
    pixel_values = TVF.pil_to_tensor(image).unsqueeze(0) / 255.0
    pixel_values = TVF.normalize(pixel_values, [0.5], [0.5])
    pixel_values = pixel_values.to('cuda')
    prompt = tokenizer.encode(prompt_str, return_tensors='pt', padding=False, truncation=False, add_special_tokens=False)
    with torch.amp.autocast_mode.autocast('cuda', enabled=True):
        vision_outputs = clip_model(pixel_values=pixel_values, output_hidden_states=True)
        image_features = vision_outputs.hidden_states
        embedded_images = image_adapter(image_features)
        embedded_images = embedded_images.to('cuda')
    prompt_embeds = text_model.model.embed_tokens(prompt.to('cuda'))
    assert prompt_embeds.shape == (1, prompt.shape[1], text_model.config.hidden_size), f"Prompt shape is {prompt_embeds.shape}, expected {(1, prompt.shape[1], text_model.config.hidden_size)}"
    embedded_bos = text_model.model.embed_tokens(torch.tensor([[tokenizer.bos_token_id]], device=text_model.device, dtype=torch.int64))
    eot_embed = image_adapter.get_eot_embedding().unsqueeze(0).to(dtype=text_model.dtype)
    inputs_embeds = torch.cat([
        embedded_bos.expand(embedded_images.shape[0], -1, -1),
        embedded_images.to(dtype=embedded_bos.dtype),
        prompt_embeds.expand(embedded_images.shape[0], -1, -1),
        eot_embed.expand(embedded_images.shape[0], -1, -1),
    ], dim=1)
    input_ids = torch.cat([
        torch.tensor([[tokenizer.bos_token_id]], dtype=torch.long),
        torch.zeros((1, embedded_images.shape[1]), dtype=torch.long),
        prompt,
        torch.tensor([[tokenizer.convert_tokens_to_ids("<|eot_id|>")]], dtype=torch.long),
    ], dim=1).to('cuda')
    attention_mask = torch.ones_like(input_ids)
    generate_ids = text_model.generate(input_ids, top_p = top_p , temperature=temperature, inputs_embeds=inputs_embeds, attention_mask=attention_mask, max_new_tokens=3000, do_sample=True, suppress_tokens=None)   # Uses the default which is temp=0.6, top_p=0.9
    generate_ids = generate_ids[:, input_ids.shape[1]:]
    if generate_ids[0][-1] == tokenizer.eos_token_id or generate_ids[0][-1] == tokenizer.convert_tokens_to_ids("<|eot_id|>"):
        generate_ids = generate_ids[:, :-1]
    caption = tokenizer.batch_decode(generate_ids, skip_special_tokens=False, clean_up_tokenization_spaces=False)[0]
    caption = f'{caption.strip()}'.replace('Prompt: Describe the image in 400 words','')
    return caption

In [ ]:
# @markdown Split the image into 20 parts prior to running
no_parts = 1 # @param {type:'slider', min:1,max:30,step:1}
print(f'Splitting all images found under /content/... \n into {no_parts} along x-axis')
import os,math
from PIL import Image
home_directory = '/content/'
using_Kaggle = os.environ.get('KAGGLE_URL_BASE','')
if using_Kaggle : home_directory = '/kaggle/working/'
%cd {home_directory}

def my_mkdirs(folder):
  if os.path.exists(folder)==False:
    os.makedirs(folder)


tgt_folder = f'/content/tmp/'
split_folder = f'/content/split/'
my_mkdirs(f'{split_folder}')


src_folder = '/content/'
suffixes = ['.gif','.png', '.jpeg' , '.webp' , '.jpg']
#num = 1
for filename in os.listdir(src_folder):
  os.remove(filename)
  continue
  for suffix in suffixes:
    if not filename.find(suffix)>-1: continue
    while os.path.exists(f'{tgt_folder}{num}.txt'):num = num+1
    print(filename)
    %cd {src_folder}
    #os.remove(f'{filename}')
    #continue
    image = Image.open(f"{filename}").convert('RGB')
    w,h=image.size
    #grid = product(range(0, h-h%d, d), range(0, w-w%d, d))
    divs=no_parts
    step=math.floor(w/divs)
    %cd {split_folder}
    for index in range(divs):
        box = (step*index, 0 ,step*(index+1),math.floor(0.8*h))
        image.crop(box).save(f'{num}_{index}.jpeg','JPEG')
    num = num+1
    #caption = stream_chat(input_image, "descriptive", "formal", "any")
    #print(f"...\n\n...caption for {filename}\n\n...")
    #print(caption)
    #---------#
    #f = open(f"{num}.txt", "w")
    #f.write(f'{caption}')
    #f.close()
    #input_image.save(f'{num}.jpeg', "JPEG")
    os.remove(f"{src_folder}{filename}")

In [ ]:

import os
from PIL import Image
home_directory = '/content/'
using_Kaggle = os.environ.get('KAGGLE_URL_BASE','')
if using_Kaggle : home_directory = '/kaggle/working/'
%cd {home_directory}

def my_mkdirs(folder):
  if os.path.exists(folder)==False:
    os.makedirs(folder)


tgt_folder = f'/content/tmp/'
my_mkdirs(f'{tgt_folder}')
split_folder = '/content/splits/'
src_folder = '/content'
if os.path.exists(f'{split_folder}'): src_folder = f'{split_folder}'
suffixes = ['.gif','.png', '.jpeg' , '.webp' , '.jpg']
num = 1
for filename in os.listdir(src_folder):
  for suffix in suffixes:
    if not filename.find(suffix)>-1: continue
    while os.path.exists(f'{tgt_folder}{num}.txt'):num = num+1
    print(filename)
    %cd {src_folder}
    input_image = Image.open(f"{filename}").convert('RGB')
    caption = stream_chat(input_image, "descriptive", "formal", "any")
    print(f"...\n\n...caption for {filename}\n\n...")
    print(caption)
    #---------#
    %cd {tgt_folder}
    f = open(f"{num}.txt", "w")
    f.write(f'{caption}')
    f.close()
    input_image.save(f'{num}.jpeg', "JPEG")
    os.remove(f"{src_folder}{filename}")
    num = num+1

In [ ]:
import shutil
%cd /content/
shutil.make_archive('/content/tmp', 'zip', '/content/tmp')

In [ ]:
# @markdown Save images of all urls found in image_urls.txt to workspace

!wget -i image_urls.txt -P ./splits



In [ ]:
# @markdown Auto-disconnect from Google Colab upon running this cell
from google.colab import runtime
#runtime.unassign() #Disconnect from runtime